# User-Interface-Demonstration

This notebook implements a user interface that allows users to select and interact with different approaches without needing to modify the underlying code. The interface provides a dropdown menu for users to select an approach (Long-context, Vanilla RAG, etc.) and a textbox for entering their queries. The selected approach and user input are processed, and the results are displayed interactively. Additionally, all user interactions are logged to facilitate user evaluations. This setup aims to streamline the experimentation process, making it more user-friendly and efficient.

# Environment Setup

* Loading the necessary packages and modules

In [6]:
# misc.
import gradio as gr
from dotenv import load_dotenv
from openai import OpenAI
from uuid import uuid4
load_dotenv()

# logging import
import logging 
logging.basicConfig(filename='user_interactions.log', level=logging.INFO)

# langchain import
from langchain_core.prompts import PromptTemplate, ChatPromptTemplate, MessagesPlaceholder
from langchain_openai import ChatOpenAI
from langchain_core.output_parsers import StrOutputParser
from langchain_core.runnables import RunnablePassthrough
import os
import requests
from getpass import getpass

# langfuse imports and tracing
from langfuse import Langfuse
from langfuse.decorators import observe
from langfuse.openai import openai

import langfuse
from langfuse import Langfuse
trace_id = str(uuid4())

LANGFUSE_SECRET_KEY = os.environ['LANGFUSE_SECRET_KEY']
LANGFUSE_PUBLIC_KEY = os.environ['LANGFUSE_PUBLIC_KEY']
LANGFUSE_HOST = "https://us.cloud.langfuse.com"

# OpenAI API Keys 
client = OpenAI(api_key=os.environ["OPENAI_API_KEY"]) 


# System Message

* Defines our system message so it is easier to manipulate going forward if needed

In [7]:
system_message = f'''''GOAL: You are a AI Legal Aid in which you play the role of specializing in end-of-life planning in Tennessee through a Q&A format. You guide users by asking clarification questions, one at a time, after they give you a response to gather necessary information and provide tailored legal advice. Your goal is to improve legal understanding and aid users in completing necessary legal documents based on their situation.

PERSONA: In this scenario, you are an AI Legal Aid in which you play the role of specializing in end-of-life planning in Tennessee. You provide expert advice on advance directives, including living wills, medical care directives, powers of attorney for healthcare, and general powers of attorney in case of incapacity. You aim to explain these concepts in simple terms, while also ensuring legal accuracy, to help users without legal training understand their options, how these documents work, and the implications of their decisions. You eventually will draft the necessary legal forms based on the information provided by users. Responses should be friendly, professional, emotionally intelligent, and engaging, making a particular effort to match the user's tone. You should break down complex legal terms into simpler concepts and provide examples where necessary to aid understanding. You should avoid overwhelming users with too many options, navigate challenging conversations gracefully and engagingly, identify areas where you can help, and lead users to the answers they need. You should probe the user for what they already know to gauge how you can be helpful, slowing down to ensure clarity and understanding. 

NARRATIVE: The user is introduced to the legal aid, who asks a set of initial questions to understand what the user wants to accomplish and determine what documents they need to fill out. You then guide and support the user to help them with their goal. 

Follow these steps in order:

STEP 1: GATHER INFORMATION
You should do this:
1. Introduce yourself: First introduce yourself to the user and tell them you are here to help them navigate their situation.
2. Ask the user the following questions. Ask these questions 1 at a time and ALWAYS wait for a response before moving on to the next question. For instance, you might ask "How can I help you navigate your legal scenario?" and the user would respond. And only then would you say "Thank you for explaining. I have another question for you to help me help you: Can you explain further...". This part of the conversations works best when you and the user take turns asking and answering questions instead of you asking a series of questions all at once. That way you can have more of a natural dialogue.

You should do this:
- Wait for a response from the user after every question before moving on.
- Work to ascertain what the user wants to accomplish specifically.
- Ask one question at a time and explain that you are asking so that you can tailor your explanation
- Gauge what the user already knows so that you can adapt your explanations and questions moving forward based on their prior knowledge.
- You should ask for any necessary clarifications to ensure the user's needs are accurately understood and addressed.

Do NOT do this:
- Start explaining right away before you gather the necessary information
- Ask the user more than 1 question at a time.

Next step: Once you have all of this information, you can move on to the next step and begin with a brief explanation

STEP 2: BEGIN DOCUMENT COMPLETION

You should do this:
Think step by step and make a plan based on the goal of the user and based on their specific scenario. Now that you know a little bit about what the user knows, consider how you will:
- Guide the user in the most efficient way possible based on the information that is needed in their specific document.
- Help the user generate answers to the necessary questions.
- Remind the user of their goal if necessary.
- Provide explanations and examples when necessary.
- Tailor your responses and questions to the user's goal and prior knowledge, which might change as the conversation progresses. 
- If applicable, use the documents uploaded in the "knowledge" section to guide your questions.

Do NOT do this:
- Provide immediate answers or solutions to problems. 
- Lose track of the user's goal and discuss other things that are off topic.

Next step: Once you have all of the necessary information for the document, move to wrap up

STEP 3: WRAP UP
You should do this:
1. Once you have all of the information needed, generate a pdf document that the user can take to the courthouse for processing in the appropriate format.
'''''

# Functions for each approach

* These cells contain the code that runs the approach that the user selects. Additionally, a global variable (llm_chat_history_lc) is initialized that allows for the chats to be logged for maintaining conversation history.

> Example function for the long-context model

In [8]:

def get_assistant_response_with_history(user_message, llm_chat_history_lc, model_name="gpt-3.5-turbo"):
    # Convert the tuple-based chat history to the appropriate format
    messages = [{'role': 'system', 'content': system_message}]
   
    for user_msg, assistant_msg in llm_chat_history_lc:
        messages.append({'role': 'user', 'content': user_msg})
        messages.append({'role': 'assistant', 'content': assistant_msg})
    
    # Add the new user message
    messages.append({'role': 'user', 'content': user_message})

    # Compute a completion (response) from the LLM
    completion = client.chat.completions.create(     
        model=model_name,
        messages=messages,
        trace_id = trace_id # assigns a specific trace id for the entire conversation so the whole conversation is grouped together
    )
    
    # Get the assistant's response
    assistant_response = completion.choices[0].message.content
    
    # Update chat history with a tuple (user_message, assistant_response)
    llm_chat_history_lc.append((user_message, assistant_response))
    
    # Return the response and updated chat history
    return assistant_response, llm_chat_history_lc


# Approach Functions

* Here, I defined each approach as their own 'approach' functions (approach_1, approach_2, etc.). In doing so, I was then able to define a function that allows the user to select which approach they would like to use.

In [9]:


# Long-context approach function defined as 'approach_1' with one parameter 'query'
def approach_1(query):
    global llm_chat_history_lc # function will use llm_chat_history_lc to maintain conversation history
    response, llm_chat_history_lc = get_assistant_response_with_history(query, llm_chat_history_lc) # calls the long context function and passes the user's query and chat history as arguments
    log_interaction("Long-Context Model", query, response) # logs the details of the interaction (the approach used, the query, and the llm's response)
    return response # returns the model's response


# Logging function to log interactions and maintain conversation history
def log_interaction(approach, query, response):
    log_entry = f"Approach: {approach}, Query: {query}, Response: {response}"
    logging.info(log_entry)

# Function that allows the user to choose an approach to get a response
def choose_approach(approach, query):
    if approach == "Long-Context Model":
        return approach_1(query)
    else:
        return "Invalid approach selected."

# Defines a list of the available approaches
approaches = ["Long-Context Model"]



# Running the Interface

* Run the following cell to interact with the interface. 
* I am using Gradio Blocks because it allows for more flexibility and customization than gradio interface. 

In [10]:

# Define the function that will be called when the user submits messages
def respond(user_message, chatbot_history):
    # Get the response from the assistant
    assistant_response, updated_history = get_assistant_response_with_history(user_message, chatbot_history)
    return "", updated_history

# Create the Gradio interface
with gr.Blocks() as demo:
    
    gr.Markdown("# Legal Empowerment Interface") # Interface Title
    gr.Markdown("### Select a model and enter your query below:") # Interface subtitle

    with gr.Row():
        with gr.Column(scale=1):
            approach_dropdown = gr.Dropdown(choices=approaches, label="Select Approach") # Creates the dropdown for selecting an approach

    chatbot_history = gr.Chatbot()  # This will store the chat history
    msg_textbox = gr.Textbox(placeholder="Type a message...")  # This is where the user types their message
    reset_button = gr.Button("Clear Chat")  # Button to clear the chat history

    # Define what happens when the user submits a message
    msg_textbox.submit(respond, inputs=[msg_textbox, chatbot_history], outputs=[msg_textbox, chatbot_history])
    
    # Define what happens when the reset button is clicked
    reset_button.click(lambda: ([], ""), outputs=[chatbot_history, msg_textbox])

    gr.Markdown("### Thank you for using our Legal Empowerment Interface!") # Closing message

# Launch the interface
demo.launch()


Running on local URL:  http://127.0.0.1:7861

To create a public link, set `share=True` in `launch()`.
